In [52]:
import pandas as pd
import regex as re

In [53]:
reviewData = pd.read_csv("ScrappedSteamReviews.csv")
reviewData

Unnamed: 0  index        games  \
0              0      0    Snakeybus   
1              1      1    Snakeybus   
2              2      2    Snakeybus   
3              3      3    Snakeybus   
4              4      4    Snakeybus   
...          ...    ...          ...   
7555        7555    205  Bloons TD 6   
7556        7556    206  Bloons TD 6   
7557        7557    207  Bloons TD 6   
7558        7558    208  Bloons TD 6   
7559        7559    209  Bloons TD 6   

                                                 review     approval  \
0     Posted: 31 December, 2019\r\nHave you ever wan...  Recommended   
1     Posted: 29 December, 2023\r\nhere to say hi to...  Recommended   
2     Posted: 13 February, 2021\r\nI bought this bec...  Recommended   
3     Posted: 28 July, 2019\r\nIt's simple and fun f...  Recommended   
4                         Posted: 22 April, 2020\r\nbus  Recommended   
...                                                 ...          ...   
7555                   Posted: August 12, 2021\r\nMONKE  Recommended   
7556  Posted: June 22, 2023\r\nTHIS IS THE MOST VIOL...  Recommended   
7557  Posted: May 17, 2022\r\nYes, I'm a simp\r\n\r\...  Recommended   
7558  Posted: January 11, 2023\r\nBloons TD 6 is a t...  Recommended   
7559  Posted: August 10, 2022\r\nUpdate, 11/26/2023:...  Recommended   

     helpCount  ComCount  
0          376         0  
1          195         0  
2          111         2  
3           98         0  
4          199         4  
...        ...       ...  
7555       232         0  
7556       217         4  
7557       181         0  
7558        88         8  
7559        76         0  

[7560 rows x 7 columns]

Add a Dates Column

In [54]:
reviewData_w_dates = reviewData
PostedDate = []

def addyear(input_date):
    #adds 2024 to dates that don't have a year atteched to them
    return(input_date + " 2024")




#iterate through each review and remove the data at the start
for i in range(len(reviewData_w_dates['review'])):

    #set a current review variable
    current = reviewData_w_dates['review'][i]

    #create several match objects
    match1 = re.search(r'Posted:\s\d{1,2} \w+', current)
    match2 = re.search(r'Posted:\s\d{1,2} \w+,\s\d{4}', current)
    match3 = re.search(r'Posted:\s\w+ \d{1,2}', current)
    match4 = re.search(r'Posted:\s\w+ \d{1,2},\s\d{4}', current)

    #match 1 and 2 have overlay 
    if match1:
        if match2: 
            PostedDate.append(match2.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = (current.replace(match2.group(), "")).lower()
        else: 
            PostedDate.append(match1.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(addyear(match1.group()), "").lower()


    if match3:
        if match4: 
            PostedDate.append(match4.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(match4.group(), "").lower()
        else: 
            PostedDate.append(match3.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(addyear(match3.group()), "").lower()

    reviewData_w_dates['review'][i] = reviewData_w_dates['review'][i].replace("\n", " ")


reviewData_w_dates['DatePosted'] = PostedDate 

len(PostedDate)


C:\Users\afvm3\AppData\Local\Temp\ipykernel_25368\1093086060.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reviewData_w_dates['review'][i] = (current.replace(match2.group(), "")).lower()
C:\Users\afvm3\AppData\Local\Temp\ipykernel_25368\1093086060.py:41: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reviewData_w_dates['review'][i] = reviewData_w_dates['review'][i].replace("\n", " ")
C:\Users\afvm3\AppData\Local\Temp\ipykernel_25368\1093086060.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-do

7560

In [55]:
reviewData_w_dates_no_d = reviewData_w_dates.drop_duplicates()
len(reviewData_w_dates_no_d)

7560

In [99]:
game_list = pd.read_csv("GamesList.csv")



gamenames = [] 
reviews = []

keywords = [
    'youtube', 'youtuber', 'video', 'channel', 'subscribe', 
    'watched', 'stream', 'streamer', 'reaction', 'playthrough',
    'let\'s play', 'review', 'gameplay', 'walkthrough', 'tutorial', 
    'live stream', 'commentary', 'episode', 'highlight', 'vlog', 
    'content creator', 'subscribe', 'subscribed', 'unboxing', 'collab', 
    'featured in', 'featured on', 'reaction video', 'uploaded', 
    'livestreamed', 'clip', 'clips', 'playback', 'fan of', 
    'mentioned in', 'shared by', "suggested"
]

for game in game_list['title']:
    checker = (reviewData_w_dates['games'] == game)
    current_game_df = reviewData_w_dates[checker]
    current_game_df.reset_index(inplace=True)

    relevant_locs = []

    for i in range(len(current_game_df)):
        rev = current_game_df["review"][i]
        rev_cleaned = re.sub(r'[^a-zA-Z0-9\s]', '', rev)
        tokenised = rev_cleaned.split(" ")
        if current_game_df["approval"][i] == "Recommended":
            for w in keywords: 
                w_lower = w.lower()
                if (w in tokenised) and i not in relevant_locs:
                        relevant_locs.append(i) 
                        gamenames.append(game)
                        reviews.append(current_game_df["review"][i])
                        break

youtube_relevant_df = pd.DataFrame({'games':gamenames, 'reviews':reviews})
print(len(reviews))

603
12


In [79]:
#watched_words = ["because of", "suggested", "video", "after", "saw", "youtube", "watched"]
keywords = [
    'youtube', 'youtuber', 'video', 'channel', 'subscribe', 
    'watched', 'stream', 'streamer', 'reaction', 'playthrough',
    'let\'s play', 'review', 'gameplay', 'walkthrough', 'tutorial', 
    'live stream', 'commentary', 'episode', 'highlight', 'vlog', 
    'content creator', 'subscribe', 'subscribed', 'unboxing', 'collab', 
    'featured in', 'featured on', 'reaction video', 'uploaded', 
    'livestreamed', 'clip', 'clips', 'playback', 'fan of', 
    'mentioned in', 'shared by', "suggested"
]

watched_words_index = []
"""
for i in range(len(reviewData_w_dates)): 
    rev = reviewData_w_dates["review"][i]
    if reviewData_w_dates["approval"][i] == "Recommended":
        for w in keywords: 
            w_lower = w.lower()
            if (re.search(rf'\b{re.escape(w_lower)}\b',rev) and i not in watched_words_index):
                    watched_words_index.append(i) 
                    break

""" 
for i in range(len(reviewData_w_dates)):
    rev = reviewData_w_dates["review"][i]
    tokenised = rev.split(" ")
    if reviewData_w_dates["approval"][i] == "Recommended":
        for w in keywords: 
            w_lower = w.lower()
            if (w in tokenised) and i not in watched_words_index:
                    watched_words_index.append(i) 
                    break


#print(reviewData_w_dates["games"][i] + ": " +rev)
len(watched_words_index)


603

In [80]:
for currentrow in reviewData_w_dates['helpCount']:
    if re.search(r"\w",currentrow): 
        print(currentrow)

376
195
111
98
199
98
68
49
196
57
98
59
75
49
52
51
40
85
40
126
42
116
35
81
36
46
46
36
35
35
31
34
29
27
26
27
36
25
72
19
31
28
36
18
25
18
14
26
17
18
28
34
28
25
17
12
193
18
15
13
24
12
15
21
20
15
13
16
16
10
16
16
13
10
14
31
20
527
26
8
10
10
14
6
12
19
11
26
9
9
48
9
19
8
16
11
11
6
6
7
11
11
6
16
15
52
19
9
10
6
8
8
12
10
7
22
14
48
11
11
13
6
12
5
9
5
10
9
5
4
25
5
11
8
6
7
6
8
5
5
20
7
9
3
6
12
10
5
4
23
12
5
6
8
3
6
4
5
8
3
5
7
7
8
3
10
11
4
3
4
17
5
10
4
5
8
4
7
5
17
4
3
5
7
2
2
4
3
6
5
5
9
8
5
4
3
7
5
4
6
4
4
4
2
3
4
3
4
8
20
100
51
54
60
67
46
32
63
38
32
104
29
29
37
257
59
32
39
22
37
26
52
58
13
19
22
21
14
14
13
21
28
17
60
20
60
15
27
11
23
10
8
47
11
11
23
12
9
10
12
10
8
9
6
12
20
9
9
6
7
10
5
8
6
5
7
7
5
9
6
6
11
5
4
9
12
5
32
6
6
6
89
27
4
14
6
4
6
4
5
4
5
5
4
4
5
11
3
6
4
4
6
5
4
6
6
3
4
6
23
11
5
4
4
5
5
3
5
15
6
7
4
3
3
3
7
3
3
4
16
4
4
14
4
7
4
9
5
3
2
4
3
4
2
4
9
4
5
5
4
4
6
7
38
2
4
5
5
2
5
4
3
2
5
6
6
2
3
3
2
3
3
5
2
2
2
3
3
2
4
2
186
5
5
5
3
4
2
19
3

In [85]:
games = [] 
revs = []
interactions = []

for i in range(len(watched_words_index)): 
    games.append(reviewData_w_dates['games'][i])
    revs.append(reviewData_w_dates['review'][i].replace("\r", ""))
    #interactions.append(int(reviewData_w_dates['helpCount'][i]) + int(reviewData_w_dates['ComCount'][i]))

youtube_df = pd.DataFrame({"games":games, "reviews":revs})
youtube_df

games                                            reviews
0       Snakeybus   have you ever wanted a version of snake with ...
1       Snakeybus   here to say hi to all the ones who watched th...
2       Snakeybus   i bought this because noodle suggested it, an...
3       Snakeybus   it's simple and fun for what it is.  if i cou...
4       Snakeybus                                                bus
..            ...                                                ...
598  Worms Rumble   i love worms, i really love worms! i have pla...
599  Worms Rumble   the game is very dynamic and fun, butthe abse...
600  Worms Rumble                      posted: may 9 this game sucks
601  Worms Rumble                                          dead game
602  Worms Rumble   this game is great. so much potential, add th...

[603 rows x 2 columns]

In [68]:
youtube_df.to_csv("steamRevsyoutube.csv")

In [98]:
game_list = pd.read_csv("GamesList.csv")
unique_games = game_list['title']
for ug in unique_games:
    count = 0
    for g in youtube_relevant_df["games"]: 
        if g == ug: 
            count = count + 1
    if count > 0: 
        print(ug +": " + str(count))

Snakeybus: 14
Biped: 19
Worms Rumble: 10
Wobbly Life: 15
Party Animals: 19
Bloons TD Battles 2: 7
PICO PARK: 4
Perfect Heist 2: 13
Goose Goose Duck: 15
Stumble Guys: 11
Bopl Battle: 17
Crab Game: 17
The Riflemen: 8
Scribblenauts Unlimited: 19
Pit People®: 30
Duck Game: 26
ShellShock Live: 13
Worms W.M.D: 19
Ratz Instagib: 10
Cat Goes Fishing: 14
The Mean Greens - Plastic Warfare: 29
Tower Unite: 25
Clustertruck: 32
Garry's Mod: 27
Who's Your Daddy?!: 11
Human Fall Flat: 16
Happy Room: 12
Pikuniku: 11
Stick Fight: The Game: 24
Worms_Ultimate_Mayhem: 13
Overcooked! 2: 9
Project Winter: 26
Super Animal Royale: 23
Pummel Party: 7
ibb & obb: 26
Bloons TD 6: 12


In [121]:
print(len(game_list))
print((game_list['title'][15]))

37
Pit People®


In [149]:
print((youtube_relevant_df["reviews"][559]))

 ☐ 10 ? / 10 }---f is a big terrarium for bugs


In [146]:
for row in range(len(youtube_relevant_df)):
    if youtube_relevant_df['games'][row] == game_list['title'][34]:
    #if re.search("youtube", rev): 
        if not("suicide" in youtube_relevant_df['reviews'][row]):
            print((youtube_relevant_df.loc[row]))

games                                           Pummel Party
reviews    \r ---{ ☑graphics☑ }---\r ☐ you forget what re...
Name: 558, dtype: object
games                                           Pummel Party
reviews    \r ---{ graphics }---\r ☐ you forget what real...
Name: 559, dtype: object
games                                           Pummel Party
reviews    \r basically a more "mature" version of mario ...
Name: 560, dtype: object
games                                           Pummel Party
reviews    posted: january 3\r ---{ gameplay }---\r ☑ ver...
Name: 561, dtype: object
games                                           Pummel Party
reviews    \r the game is really fun playing with friends...
Name: 562, dtype: object
games                                           Pummel Party
reviews    \r pummel party is a mario party-type party ga...
Name: 563, dtype: object
games                                           Pummel Party
reviews    \r unfortunately, you cannot play with one key

Data Inspection for analysi sof mentioned youtubers

In [153]:
for row in range(len(youtube_relevant_df)):
    if youtube_relevant_df['games'][row] == game_list['title'][36]:
    #if re.search("youtube", rev): 
        if not("suicide" in youtube_relevant_df['reviews'][row]):
            print((youtube_relevant_df['reviews'][row]))

 is this really the end?s of filthy and paltry casual gameplay. you've played this monkey game for so many hours that all the endless chasing of top 3 medals and pushing of the skill ceiling has become... meaningless. you've already done it all and yet you've accomplished... nothing. what is there left to do other than make meme custom maps, impossible challenges and play c.h.i.m.p.s. on "your mom but at a different angle"? or as dj benjamin says, "turn up the double cash!"s becomes cuddles. custom challenges become trivial too. 2tc is a joke. try half cash c.h.i.m.p.s. on rake. your favorite hero is adora, because you did 2mpc on x factor with her. this playtime. you tap into secret knowledge known only to the most elite high-level bloons players and think of completely new ways of understanding different parts of the game. mastered mortar micro? try ace micro. haven't heard of rng-manip in bloons? maybe you'll be the first to discover it. you start to question your favorite hero, bec

In [154]:
Mentioned_youtubers = ["Dank Pods", "Noodle", "Dantdm", "PewDiePie", "BulletBarry", "Jacksepticeye"]